In [1]:
from typing import List, Optional, Any
import torch
import torch.utils.data
import numpy as np
import random

import datetime

import transformers
from transformers import AutoTokenizer, AutoModelForCausalLM, BitsAndBytesConfig

from peft import LoraConfig
from trl import SFTTrainer
import datasets
import time

import json
import os
import cqlcmp

In [2]:
torch.manual_seed(21)
torch.cuda.manual_seed_all(21)
np.random.seed(21)
random.seed(21)
#torch.backends.cudnn.deterministic = True
#torch.backends.cudnn.benchmark = False

In [3]:
device = torch.device("cuda")

In [4]:
class DatasetNatural2CQL(torch.utils.data.Dataset):
    def __init__(self, path: Optional[str] = None) -> None:
        self.sentence_freq = []
        self.cql2nl = []
        self.nl2cql = []
        self.natural_language_rulebased = []
        self.cql = []
        self.natural_language = []
        self.enabled_natural_language = []

        if path is not None:
            self.load_tsv(path)

    def enable_cql(self, cqls):
        self.enabled_natural_language = []
        for cql in cqls:
            for p in cql:
                self.enabled_natural_language.append(p)

    def dump_json(self, filepath: str) -> None:
        with open(filepath, "w") as file:
            for i in range(len(self)):
                data = json.dumps(self[i])
                file.write(data)
                file.write("\n")

    def add_translation(self, freq: int, cql: str, natural_language_rulebased: str, natural_language: List[str]) -> None:
        cql_index = len(self.sentence_freq)
        self.sentence_freq.append(freq)
        self.cql.append(cql)
        self.natural_language_rulebased.append(natural_language_rulebased)
        self.cql2nl.append([])

        for sentence in natural_language:
            self.nl2cql.append(cql_index)
            self.cql2nl[-1].append(len(self.natural_language))
            self.natural_language.append(sentence)

    def load_tsv(self, path: str) -> None:
        with open(path, "r") as file_data:
            for line in file_data:
                line = line.strip()
                line = line.split("\t")
                texts_json = json.loads(line[4])
                texts_extracted = texts_json["data"][0]["content"][0]["text"]["value"].split("\n")
                self.add_translation(int(line[0]), line[2], line[3], texts_extracted)

    def __len__(self):
        return len(self.enabled_natural_language)

    def __getitem__(self, idx):
        if idx < len(self.nl2cql):
            return {"text": self.natural_language[self.enabled_natural_language[idx]], "cql": self.cql[self.nl2cql[self.enabled_natural_language[idx]]]}
        return None

In [5]:
dataset = DatasetNatural2CQL("expand_natural_texts_0004.res.tsv")

In [6]:
validation_cqls = []
with open("test_ids.json", "r") as file:
    validation_cqls = json.load(file)

In [7]:
dataset.enable_cql(validation_cqls)

In [8]:
from transformers import AutoModelForCausalLM, AutoTokenizer

base_model_name = "meta-llama/Llama-3.2-1B"

bnb_config = BitsAndBytesConfig(
    load_in_4bit=True,
    bnb_4bit_quant_type="nf4",
    bnb_4bit_compute_dtype=torch.bfloat16
)

model = AutoModelForCausalLM.from_pretrained(base_model_name, quantization_config=bnb_config, device_map={"":0})
model = model.to(device)

tokenizer = AutoTokenizer.from_pretrained(base_model_name)

In [9]:
def f_in(data):
    full_input = """Translate Natural Language into CQL Queries like:

Word dog followed by lemma run, and then followed by a noun. CQL:
```
[word="dog"][lemma="run"][pos="NN"]
```

Lemma "be" optionally followed by the word "not". CQL:
```
[lemma="be"][word="not"]? 
```

""" + data + " CQL:\n```\n"
    return full_input

In [10]:
# random.shuffle(dataset.enabled_natural_language)

i = 0
while i < len(dataset):
    dataset.natural_language[dataset.enabled_natural_language[i]] = f_in(dataset.natural_language[dataset.enabled_natural_language[i]])
    i += 1

In [11]:
tokenizer.pad_token = tokenizer.eos_token

In [12]:
def get_cql(text):
    text = text.split("<eos>")[0]
    text = text.split("CQL:")[3]
    text = text.split("```")[1]
    return text.strip()

In [13]:
def get_text(text):
    text = text = text.split("CQL:")[2]
    text = text = text.split("```")[-1]
    return text.strip()

In [14]:
with open("test_results.tsv", "w") as test_tsv:
    with open("test_log.txt", "w") as log:
        start_time = int(time.time())
        
        dataloader = torch.utils.data.DataLoader(dataset, batch_size=256, shuffle=False)
        blue_sum = 0
        blue_size = 0
        batch_id = 0
        for batch in dataloader:
            batch_id += 1
            inputs = tokenizer(batch["text"], truncation=True, max_length=1024, return_tensors="pt", padding=True).to(device)
            outputs = model.generate(**inputs, max_new_tokens=100)
            for i, output in enumerate(outputs):
                cql = get_cql(tokenizer.decode(output, skip_special_tokens=True))
                cql_ids = cqlcmp.cql_tokenizer(cql)
                gold_cql_ids = cqlcmp.cql_tokenizer(batch["cql"][i])
                bleu = cqlcmp.sentence_bleu([gold_cql_ids], cql_ids, weights=(0.25, 0.25, 0.25, 0.25))
                blue_sum += bleu
                blue_size += 1
                test_result = [cql.replace("\n", " "), batch["cql"][i], get_text(batch["text"][i])]
                print("\t".join(test_result))
                print("\t".join(test_result), file=test_tsv)
            to_log = ""
            to_log += "Working on: " + "baseline" + " | "
            to_log += str(blue_size) + "/" + str(len(dataset)) + " | "
            to_log += "AVG Bleu: " + str(blue_sum/blue_size) + " | "
            to_log += "Time: " + str(int(time.time())-start_time) + " | "
            to_log += "ETA: " + str(int((int(time.time())-start_time)/(blue_size/len(dataset)*(1-(blue_size/len(dataset)))))) + " sec" + " | "
            
            print(to_log, file=log)
            log.flush()
            test_tsv.flush()
            print(to_log)
            

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.
/mnt/asteria02/thor1/asteria04_mnt_local2/xmikusek/aiproject/.venv/lib/python3.10/site-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 2-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/mnt/asteria02/thor1/asteria04_mnt_local2/xmikusek/aiproject/.venv/lib/python3.10/site-packages/nltk/translate/bleu_score.py:577: UserWarning: 
The hypothesis contains 0 counts of 3-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunct

	[tag !="DT" & tag !="JJ.*" & tag !="CD" & tag !="N.*"] [word="man"]	All tokens that are not determiners, adjectives, cardinal numbers, or nouns followed by the word "man."
	[tag !="DT" & tag !="JJ.*" & tag !="CD" & tag !="N.*"] [word="man"]	Any token that does not match the tags DT, JJ, CD, or is not a noun, followed by the word "man."
- [non-determiner]	[tag !="DT" & tag !="JJ.*" & tag !="CD" & tag !="N.*"] [word="man"]	Non-determiner, non-adjective, non-number, and non-noun tokens that precede the word "man."
by[not[lemma="man"]][not[lemma="dog"]][not[lemma="cat"]]	[tag !="DT" & tag !="JJ.*" & tag !="CD" & tag !="N.*"] [word="man"]	Tokens excluding determiners, adjectives, numbers, and nouns followed by "man."
	[tag !="DT" & tag !="JJ.*" & tag !="CD" & tag !="N.*"] [word="man"]	Any token that is not tagged as DT, JJ, CD, or is a noun right before the word "man."
	[tag !="DT" & tag !="JJ.*" & tag !="CD" & tag !="N.*"] [word="man"]	A sequence where the preceding token fits none of the

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.


The verb "to be" is followed by "not" or "not".	[lempos="determine-v"]	Forms of the verb determine.
We need to look for a verb form.	[lempos="determine-v"]	Only verb forms determine.
	[lempos="determine-v"]	All lexemes for the verb 'determine'.
#verb	[lempos="determine-v"]	Any verb forms of determine.
lemma=verb	[lempos="determine-v"]	Lexical items with the verb lemma determine.
#lemma	[lempos="determine-v"]	All occurrences of the verb lemma as determine.
-lemma="determine"	[lempos="determine-v"]	Lexical forms labeled as determine in verb category.
1. [word="s?pr?l?ay"]	[word= "s?pr?l?ay"]	Any word that matches the pattern s?pr?l?ay.
	[word= "s?pr?l?ay"]	Words that contain variations of "spray."
-lemma="s" or lemma="pr" or lemma="l" or lemma="ay"	[word= "s?pr?l?ay"]	Words before or after a possible 's', 'pr', 'l', or 'ay'.
This word is not a valid CQL query.	[word= "s?pr?l?ay"]	Words resembling the spelling of "spray".
	[word= "s?pr?l?ay"]	All words that include 'spray' with optional p

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.


...

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.


# want # [preposition] # verb # in # the # present # participle # form	[lemma="want"] [tag="PP"] [tag="VBG"]	The token want followed by a preposition and then a verb in the present participle form.
\[     [want="want"][prep="want"][action="want"] ]	[lemma="want"] [tag="PP"] [tag="VBG"]	Query for want followed by a preposition and then a continuous action (VBG).
In the phrase "want to", "wanting to" or "wanting" followed by a verb in the gerund.	[lemma="want"] [tag="PP"] [tag="VBG"]	Occurrences of the lemma want and then a phrase indicating a preposition followed by a verb in the gerund.
	[lemma="open"]	Lemma open.
\{lemma="open"}/	[lemma="open"]	Token with lemma open.
The word "open" or "openness"	[lemma="open"]	All instances of the lemma open.
	[lemma="open"]	Any form of open as lemma.
The word "open" followed by a noun.	[lemma="open"]	Tokens containing the lemma open.
	[lemma="open"]	Base form of the word open.
	[lemma="open"]	Occurrences of open as a lemma.
# lemma "be" open	[lemma=

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.


#verb_tagged_as[verb_tagged_as="able"][verb_tagged_as="to"]#	[tag="VB|VBD|VBG|VBN|VBP|VBZ"][word="able"][word="to"]	Words tagged as verbs that directly precede "able" and "to".
We can say: [verb1:able][verb2:to]	[tag="VB|VBD|VBG|VBN|VBP|VBZ"][word="able"][word="to"]	A sequence of verbs followed by the word "able" and the word "to".
\verb[verb1\verb[verb2\verb[verb3]]	[tag="VB|VBD|VBG|VBN|VBP|VBZ"][word="able"][word="to"]	Tokens of various verb forms leading into "able" and "to".
	[tag="VB|VBD|VBG|VBN|VBP|VBZ"][word="able"][word="to"]	Instances where a verb comes before "able", followed by "to".
- [verb:able] - [verb:to] - [word="to" - [word="able"]	[tag="VB|VBD|VBG|VBN|VBP|VBZ"][word="able"][word="to"]	Verbs in any of the specified forms preceding "able" and "to".
The verb "able" followed by "to" and a noun.	[tag="VB|VBD|VBG|VBN|VBP|VBZ"][word="able"][word="to"]	Verbs that relate to "able" and are followed by "to".
1. verb form "able" + "to" + "able" + "to" + "able" + "to" + "able" + "

ZeroDivisionError: float division by zero